In [1]:
import numpy as np
import pandas as pd
import timeit
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from sklearn.cluster import DBSCAN

%alias_magic t timeit

# import warnings filter
from warnings import simplefilter
# ignore all future warnings
simplefilter(action='ignore', category=FutureWarning)


Created `%t` as an alias for `%timeit`.
Created `%%t` as an alias for `%%timeit`.


In [3]:
data = pd.read_csv(r'C:\Users\Saba\Documents\ML project\Full_particle_Data\particles_information.csv')
data.info()
data.describe()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19683000 entries, 0 to 19682999
Data columns (total 10 columns):
snapnum    int64
phkey      int64
x          float64
y          float64
z          float64
vx         float64
vy         float64
vz         float64
id         int64
In_halo    int64
dtypes: float64(6), int64(4)
memory usage: 1.5 GB


snapnum         phkey             x             y             z  \
count  19683000.0  1.968300e+07  1.968300e+07  1.968300e+07  1.968300e+07   
mean          0.0  1.637668e+04  3.127470e+01  3.124592e+01  3.122501e+01   
std           0.0  9.453553e+03  1.804878e+01  1.804944e+01  1.802320e+01   
min           0.0  0.000000e+00  5.066395e-07  0.000000e+00  3.213994e-06   
25%           0.0  8.202000e+03  1.564608e+01  1.561590e+01  1.563889e+01   
50%           0.0  1.635500e+04  3.130093e+01  3.123226e+01  3.119702e+01   
75%           0.0  2.455900e+04  4.690146e+01  4.689474e+01  4.681961e+01   
max           0.0  3.276700e+04  6.250000e+01  6.250000e+01  6.250000e+01   

                 vx            vy            vz            id       In_halo  
count  1.968300e+07  1.968300e+07  1.968300e+07  1.968300e+07  1.968300e+07  
mean  -2.781189e-04  2.267425e-04 -4.716782e-05  9.841500e+06  2.833979e-01  
std    2.414422e+02  2.154665e+02  2.888102e+02  5.681993e+06  4.506479e-01  
min   -9.472481e+02 -1.023661e+03 -9.789142e+02  1.000000e+00  0.000000e+00  
25%   -1.623357e+02 -1.451293e+02 -2.172641e+02  4.920751e+06  0.000000e+00  
50%    6.388357e-01  3.100713e-01 -3.280887e+00  9.841500e+06  0.000000e+00  
75%    1.639600e+02  1.479353e+02  2.112060e+02  1.476225e+07  1.000000e+00  
max    8.930905e+02  9.109451e+02  1.070528e+03  1.968300e+07  1.000000e+00

In [5]:
in_halo = pd.read_csv(r'C:\Users\Saba\Documents\ML project\Full_particle_Data\IN_Halo.csv', skiprows = 9)
in_halo.info()
in_halo.describe()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5578120 entries, 0 to 5578119
Data columns (total 4 columns):
particleId    int64
subhaloId     int64
np            int64
redshift      float64
dtypes: float64(1), int64(3)
memory usage: 170.2 MB


particleId     subhaloId            np   redshift
count  5.578120e+06  5.578120e+06  5.578120e+06  5578120.0
mean   9.544373e+06  6.300031e+13  2.874144e+04        0.0
std    5.458220e+06  1.980625e+08  3.229014e+04        0.0
min    2.000000e+00  6.300000e+13  1.602000e+03        0.0
25%    5.129375e+06  6.300020e+13  5.658000e+03        0.0
50%    8.975824e+06  6.300030e+13  1.640700e+04        0.0
75%    1.397106e+07  6.300050e+13  3.824700e+04        0.0
max    1.968300e+07  6.300070e+13  1.372720e+05        0.0

In [51]:
id_all_index = np.array(data[['id', 'In_halo']].sort_values('id'))

print(id_all_index)

[[       1        0]
 [       2        1]
 [       3        0]
 ...
 [19682998        0]
 [19682999        1]
 [19683000        1]]


In [10]:
print('All INs',len(id_all_index[id_all_index[:,1] == 1]))
print('All OUTs',len(id_all_index[id_all_index[:,1] == 0]))

All INs 5578120
All OUTs 14104880


In [52]:
all_out = data.loc[data['In_halo'] == 0]
all_out.info()
all_out.describe()
print(all_out)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 14104880 entries, 0 to 19682997
Data columns (total 10 columns):
snapnum    int64
phkey      int64
x          float64
y          float64
z          float64
vx         float64
vy         float64
vz         float64
id         int64
In_halo    int64
dtypes: float64(6), int64(4)
memory usage: 1.2 GB
          snapnum  phkey         x          y          z         vx  \
0               0      0  0.079177   0.003392   0.416711   6.259036   
2               0      0  0.262699   0.197281   0.224564  32.359110   
7               0      0  0.066026   0.232851   0.100297  99.861310   
9               0      0  0.127710   0.883628   0.166871  82.522514   
13              0      0  0.331709   0.773337   0.294924  32.026170   
...           ...    ...       ...        ...        ...        ...   
19682993        0  32767  0.265102   0.255621  62.154778  79.569190   
19682994        0  32767  0.438595   0.313664  62.455310 -13.440866   
19682995      

In [54]:
all_in = data.loc[data['In_halo'] == 1]
all_in.info()
all_in.describe()
print(all_in)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5578120 entries, 1 to 19682999
Data columns (total 10 columns):
snapnum    int64
phkey      int64
x          float64
y          float64
z          float64
vx         float64
vy         float64
vz         float64
id         int64
In_halo    int64
dtypes: float64(6), int64(4)
memory usage: 468.1 MB
          snapnum  phkey         x         y          z          vx  \
1               0      0  0.289189  0.130278   0.456327    7.491590   
3               0      0  0.240575  0.396040   0.038927   67.365524   
4               0      0  0.408888  0.367119   0.182086  -14.317771   
5               0      0  0.403685  0.353911   0.453980  -10.978485   
6               0      0  0.093024  0.249419   0.381685   53.162210   
...           ...    ...       ...       ...        ...         ...   
19682987        0  32767  0.331488  0.464647  62.296314   51.349228   
19682990        0  32767  0.153362  0.597256  62.431736  117.202385   
19682992     

In [55]:
mass = np.array(in_halo[['particleId', 'np']].sort_values('particleId'))
new_index = np.zeros(len(mass))
print('new indexes:', new_index)
print('halo mass and ids: ', mass)

for i in range(len(mass)):
    if mass[i,1] < 40600:
        new_index[i] = int( (mass[i,1]-1600) / 1000 ) + 1
    else:
        new_index[i] = 40
        
print(new_index)

new indexes: [0. 0. 0. ... 0. 0. 0.]
halo mass and ids:  [[       2    25323]
 [       4    25323]
 [       5    78803]
 ...
 [19682993    25323]
 [19682999    25323]
 [19683000    25323]]
[24. 24. 40. ... 24. 24. 24.]


In [56]:
#The new index which have been made this way is sorted bythe ids just the way as the all_in dataframe
print('total size:', len(new_index))
print('Maximum value:', max(new_index))
print('Minimum value:', min(new_index))

total size: 5578120
Maximum value: 40.0
Minimum value: 1.0


In [57]:
for j in range(40):
    n = j+1
    print(n, 'class size:' , len(new_index[new_index == n]) )


1 class size: 500201
2 class size: 338830
3 class size: 303439
4 class size: 233739
5 class size: 249290
6 class size: 131822
7 class size: 174988
8 class size: 72600
9 class size: 160739
10 class size: 110242
11 class size: 60626
12 class size: 117000
13 class size: 112986
14 class size: 121636
15 class size: 129450
16 class size: 85407
17 class size: 108362
18 class size: 76886
19 class size: 101145
20 class size: 63894
21 class size: 44127
22 class size: 114071
23 class size: 24576
24 class size: 50538
25 class size: 52024
26 class size: 54827
27 class size: 27620
28 class size: 58313
29 class size: 59481
30 class size: 62902
31 class size: 32218
32 class size: 33174
33 class size: 135998
34 class size: 139802
35 class size: 0
36 class size: 36717
37 class size: 38247
38 class size: 39550
39 class size: 80108
40 class size: 1240545


In [38]:
num_halo = 0
for i in range(1600,137273,1):
    l = len(mass[mass[:,1] == i])
    num = l/i
    num_halo += num
    print('number of halos with mass ', i , 'is:' , num )

print('number_of_halos:', num_halo)

number of halos with mass  1600 is: 0.0
number of halos with mass  1601 is: 0.0
number of halos with mass  1602 is: 1.0
number of halos with mass  1603 is: 0.0
number of halos with mass  1604 is: 1.0
number of halos with mass  1605 is: 0.0
number of halos with mass  1606 is: 0.0
number of halos with mass  1607 is: 1.0
number of halos with mass  1608 is: 0.0
number of halos with mass  1609 is: 0.0
number of halos with mass  1610 is: 1.0
number of halos with mass  1611 is: 1.0
number of halos with mass  1612 is: 1.0
number of halos with mass  1613 is: 0.0
number of halos with mass  1614 is: 3.0
number of halos with mass  1615 is: 0.0
number of halos with mass  1616 is: 0.0
number of halos with mass  1617 is: 0.0
number of halos with mass  1618 is: 0.0
number of halos with mass  1619 is: 0.0
number of halos with mass  1620 is: 0.0
number of halos with mass  1621 is: 0.0
number of halos with mass  1622 is: 0.0
number of halos with mass  1623 is: 0.0
number of halos with mass  1624 is: 0.0


number of halos with mass  1810 is: 0.0
number of halos with mass  1811 is: 0.0
number of halos with mass  1812 is: 0.0
number of halos with mass  1813 is: 1.0
number of halos with mass  1814 is: 0.0
number of halos with mass  1815 is: 0.0
number of halos with mass  1816 is: 0.0
number of halos with mass  1817 is: 0.0
number of halos with mass  1818 is: 0.0
number of halos with mass  1819 is: 0.0
number of halos with mass  1820 is: 0.0
number of halos with mass  1821 is: 0.0
number of halos with mass  1822 is: 0.0
number of halos with mass  1823 is: 1.0
number of halos with mass  1824 is: 0.0
number of halos with mass  1825 is: 2.0
number of halos with mass  1826 is: 0.0
number of halos with mass  1827 is: 0.0
number of halos with mass  1828 is: 0.0
number of halos with mass  1829 is: 0.0
number of halos with mass  1830 is: 1.0
number of halos with mass  1831 is: 0.0
number of halos with mass  1832 is: 0.0
number of halos with mass  1833 is: 1.0
number of halos with mass  1834 is: 0.0


number of halos with mass  2025 is: 0.0
number of halos with mass  2026 is: 0.0
number of halos with mass  2027 is: 0.0
number of halos with mass  2028 is: 0.0
number of halos with mass  2029 is: 1.0
number of halos with mass  2030 is: 0.0
number of halos with mass  2031 is: 0.0
number of halos with mass  2032 is: 0.0
number of halos with mass  2033 is: 0.0
number of halos with mass  2034 is: 0.0
number of halos with mass  2035 is: 0.0
number of halos with mass  2036 is: 0.0
number of halos with mass  2037 is: 0.0
number of halos with mass  2038 is: 0.0
number of halos with mass  2039 is: 1.0
number of halos with mass  2040 is: 0.0
number of halos with mass  2041 is: 1.0
number of halos with mass  2042 is: 0.0
number of halos with mass  2043 is: 0.0
number of halos with mass  2044 is: 0.0
number of halos with mass  2045 is: 0.0
number of halos with mass  2046 is: 0.0
number of halos with mass  2047 is: 0.0
number of halos with mass  2048 is: 0.0
number of halos with mass  2049 is: 0.0


number of halos with mass  2240 is: 0.0
number of halos with mass  2241 is: 0.0
number of halos with mass  2242 is: 1.0
number of halos with mass  2243 is: 0.0
number of halos with mass  2244 is: 0.0
number of halos with mass  2245 is: 0.0
number of halos with mass  2246 is: 0.0
number of halos with mass  2247 is: 0.0
number of halos with mass  2248 is: 0.0
number of halos with mass  2249 is: 1.0
number of halos with mass  2250 is: 0.0
number of halos with mass  2251 is: 1.0
number of halos with mass  2252 is: 0.0
number of halos with mass  2253 is: 0.0
number of halos with mass  2254 is: 0.0
number of halos with mass  2255 is: 0.0
number of halos with mass  2256 is: 1.0
number of halos with mass  2257 is: 1.0
number of halos with mass  2258 is: 0.0
number of halos with mass  2259 is: 0.0
number of halos with mass  2260 is: 0.0
number of halos with mass  2261 is: 0.0
number of halos with mass  2262 is: 0.0
number of halos with mass  2263 is: 0.0
number of halos with mass  2264 is: 0.0


number of halos with mass  2454 is: 0.0
number of halos with mass  2455 is: 0.0
number of halos with mass  2456 is: 0.0
number of halos with mass  2457 is: 0.0
number of halos with mass  2458 is: 0.0
number of halos with mass  2459 is: 1.0
number of halos with mass  2460 is: 0.0
number of halos with mass  2461 is: 0.0
number of halos with mass  2462 is: 0.0
number of halos with mass  2463 is: 0.0
number of halos with mass  2464 is: 0.0
number of halos with mass  2465 is: 1.0
number of halos with mass  2466 is: 0.0
number of halos with mass  2467 is: 1.0
number of halos with mass  2468 is: 0.0
number of halos with mass  2469 is: 0.0
number of halos with mass  2470 is: 0.0
number of halos with mass  2471 is: 0.0
number of halos with mass  2472 is: 0.0
number of halos with mass  2473 is: 1.0
number of halos with mass  2474 is: 0.0
number of halos with mass  2475 is: 0.0
number of halos with mass  2476 is: 0.0
number of halos with mass  2477 is: 0.0
number of halos with mass  2478 is: 0.0


...

number of halos with mass  136243 is: 0.0
number of halos with mass  136244 is: 0.0
number of halos with mass  136245 is: 0.0
number of halos with mass  136246 is: 0.0
number of halos with mass  136247 is: 0.0
number of halos with mass  136248 is: 0.0
number of halos with mass  136249 is: 0.0
number of halos with mass  136250 is: 0.0
number of halos with mass  136251 is: 0.0
number of halos with mass  136252 is: 0.0
number of halos with mass  136253 is: 0.0
number of halos with mass  136254 is: 0.0
number of halos with mass  136255 is: 0.0
number of halos with mass  136256 is: 0.0
number of halos with mass  136257 is: 0.0
number of halos with mass  136258 is: 0.0
number of halos with mass  136259 is: 0.0
number of halos with mass  136260 is: 0.0
number of halos with mass  136261 is: 0.0
number of halos with mass  136262 is: 0.0
number of halos with mass  136263 is: 0.0
number of halos with mass  136264 is: 0.0
number of halos with mass  136265 is: 0.0
number of halos with mass  136266 

number of halos with mass  136452 is: 0.0
number of halos with mass  136453 is: 0.0
number of halos with mass  136454 is: 0.0
number of halos with mass  136455 is: 0.0
number of halos with mass  136456 is: 0.0
number of halos with mass  136457 is: 0.0
number of halos with mass  136458 is: 0.0
number of halos with mass  136459 is: 0.0
number of halos with mass  136460 is: 0.0
number of halos with mass  136461 is: 0.0
number of halos with mass  136462 is: 0.0
number of halos with mass  136463 is: 0.0
number of halos with mass  136464 is: 0.0
number of halos with mass  136465 is: 0.0
number of halos with mass  136466 is: 0.0
number of halos with mass  136467 is: 0.0
number of halos with mass  136468 is: 0.0
number of halos with mass  136469 is: 0.0
number of halos with mass  136470 is: 0.0
number of halos with mass  136471 is: 0.0
number of halos with mass  136472 is: 0.0
number of halos with mass  136473 is: 0.0
number of halos with mass  136474 is: 0.0
number of halos with mass  136475 

number of halos with mass  136660 is: 0.0
number of halos with mass  136661 is: 0.0
number of halos with mass  136662 is: 0.0
number of halos with mass  136663 is: 0.0
number of halos with mass  136664 is: 0.0
number of halos with mass  136665 is: 0.0
number of halos with mass  136666 is: 0.0
number of halos with mass  136667 is: 0.0
number of halos with mass  136668 is: 0.0
number of halos with mass  136669 is: 0.0
number of halos with mass  136670 is: 0.0
number of halos with mass  136671 is: 0.0
number of halos with mass  136672 is: 0.0
number of halos with mass  136673 is: 0.0
number of halos with mass  136674 is: 0.0
number of halos with mass  136675 is: 0.0
number of halos with mass  136676 is: 0.0
number of halos with mass  136677 is: 0.0
number of halos with mass  136678 is: 0.0
number of halos with mass  136679 is: 0.0
number of halos with mass  136680 is: 0.0
number of halos with mass  136681 is: 0.0
number of halos with mass  136682 is: 0.0
number of halos with mass  136683 

number of halos with mass  136876 is: 0.0
number of halos with mass  136877 is: 0.0
number of halos with mass  136878 is: 0.0
number of halos with mass  136879 is: 0.0
number of halos with mass  136880 is: 0.0
number of halos with mass  136881 is: 0.0
number of halos with mass  136882 is: 0.0
number of halos with mass  136883 is: 0.0
number of halos with mass  136884 is: 0.0
number of halos with mass  136885 is: 0.0
number of halos with mass  136886 is: 0.0
number of halos with mass  136887 is: 0.0
number of halos with mass  136888 is: 0.0
number of halos with mass  136889 is: 0.0
number of halos with mass  136890 is: 0.0
number of halos with mass  136891 is: 0.0
number of halos with mass  136892 is: 0.0
number of halos with mass  136893 is: 0.0
number of halos with mass  136894 is: 0.0
number of halos with mass  136895 is: 0.0
number of halos with mass  136896 is: 0.0
number of halos with mass  136897 is: 0.0
number of halos with mass  136898 is: 0.0
number of halos with mass  136899 

number of halos with mass  137085 is: 0.0
number of halos with mass  137086 is: 0.0
number of halos with mass  137087 is: 0.0
number of halos with mass  137088 is: 0.0
number of halos with mass  137089 is: 0.0
number of halos with mass  137090 is: 0.0
number of halos with mass  137091 is: 0.0
number of halos with mass  137092 is: 0.0
number of halos with mass  137093 is: 0.0
number of halos with mass  137094 is: 0.0
number of halos with mass  137095 is: 0.0
number of halos with mass  137096 is: 0.0
number of halos with mass  137097 is: 0.0
number of halos with mass  137098 is: 0.0
number of halos with mass  137099 is: 0.0
number of halos with mass  137100 is: 0.0
number of halos with mass  137101 is: 0.0
number of halos with mass  137102 is: 0.0
number of halos with mass  137103 is: 0.0
number of halos with mass  137104 is: 0.0
number of halos with mass  137105 is: 0.0
number of halos with mass  137106 is: 0.0
number of halos with mass  137107 is: 0.0
number of halos with mass  137108 

In [58]:
new_all_in = all_in.drop(columns = 'In_halo')
new_all_in.info()
new_all_in.describe()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5578120 entries, 1 to 19682999
Data columns (total 9 columns):
snapnum    int64
phkey      int64
x          float64
y          float64
z          float64
vx         float64
vy         float64
vz         float64
id         int64
dtypes: float64(6), int64(3)
memory usage: 425.6 MB


snapnum         phkey             x             y             z  \
count  5578120.0  5.578120e+06  5.578120e+06  5.578120e+06  5.578120e+06   
mean         0.0  1.588373e+04  3.256544e+01  3.098034e+01  2.933547e+01   
std          0.0  9.078947e+03  1.829662e+01  1.850417e+01  1.695026e+01   
min          0.0  0.000000e+00  3.814697e-06  1.907349e-05  1.432467e-05   
25%          0.0  8.621000e+03  1.751555e+01  1.489436e+01  1.558683e+01   
50%          0.0  1.493500e+04  3.363033e+01  2.999991e+01  2.801594e+01   
75%          0.0  2.323000e+04  4.806306e+01  4.819264e+01  4.222892e+01   
max          0.0  3.276700e+04  6.249999e+01  6.249999e+01  6.249996e+01   

                 vx            vy            vz            id  
count  5.578120e+06  5.578120e+06  5.578120e+06  5.578120e+06  
mean  -3.783877e+00 -3.493404e-01  6.013589e+00  9.544373e+06  
std    2.557795e+02  2.321931e+02  3.005060e+02  5.458220e+06  
min   -9.472481e+02 -1.023661e+03 -9.789142e+02  2.000000e+00  
25%   -1.791693e+02 -1.593411e+02 -2.110390e+02  5.129375e+06  
50%   -2.128368e-01 -1.632185e+00  5.875571e+00  8.975824e+06  
75%    1.708659e+02  1.610524e+02  2.205653e+02  1.397106e+07  
max    8.927465e+02  8.821260e+02  1.070528e+03  1.968300e+07

In [59]:
new_all_in['In_halo'] = new_index
new_all_in['halo_mass'] = mass[:,1]
new_all_in['id-prime'] = mass[:,0]
new_all_in.info()
new_all_in.describe()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5578120 entries, 1 to 19682999
Data columns (total 12 columns):
snapnum      int64
phkey        int64
x            float64
y            float64
z            float64
vx           float64
vy           float64
vz           float64
id           int64
In_halo      float64
halo_mass    int64
id-prime     int64
dtypes: float64(7), int64(5)
memory usage: 553.2 MB


snapnum         phkey             x             y             z  \
count  5578120.0  5.578120e+06  5.578120e+06  5.578120e+06  5.578120e+06   
mean         0.0  1.588373e+04  3.256544e+01  3.098034e+01  2.933547e+01   
std          0.0  9.078947e+03  1.829662e+01  1.850417e+01  1.695026e+01   
min          0.0  0.000000e+00  3.814697e-06  1.907349e-05  1.432467e-05   
25%          0.0  8.621000e+03  1.751555e+01  1.489436e+01  1.558683e+01   
50%          0.0  1.493500e+04  3.363033e+01  2.999991e+01  2.801594e+01   
75%          0.0  2.323000e+04  4.806306e+01  4.819264e+01  4.222892e+01   
max          0.0  3.276700e+04  6.249999e+01  6.249999e+01  6.249996e+01   

                 vx            vy            vz            id       In_halo  \
count  5.578120e+06  5.578120e+06  5.578120e+06  5.578120e+06  5.578120e+06   
mean  -3.783877e+00 -3.493404e-01  6.013589e+00  9.544373e+06  1.911223e+01   
std    2.557795e+02  2.321931e+02  3.005060e+02  5.458220e+06  1.498567e+01   
min   -9.472481e+02 -1.023661e+03 -9.789142e+02  2.000000e+00  1.000000e+00   
25%   -1.791693e+02 -1.593411e+02 -2.110390e+02  5.129375e+06  5.000000e+00   
50%   -2.128368e-01 -1.632185e+00  5.875571e+00  8.975824e+06  1.500000e+01   
75%    1.708659e+02  1.610524e+02  2.205653e+02  1.397106e+07  3.700000e+01   
max    8.927465e+02  8.821260e+02  1.070528e+03  1.968300e+07  4.000000e+01   

          halo_mass      id-prime  
count  5.578120e+06  5.578120e+06  
mean   2.874144e+04  9.544373e+06  
std    3.229014e+04  5.458220e+06  
min    1.602000e+03  2.000000e+00  
25%    5.658000e+03  5.129375e+06  
50%    1.640700e+04  8.975824e+06  
75%    3.824700e+04  1.397106e+07  
max    1.372720e+05  1.968300e+07

In [60]:
#for making sure that ids and id-primes are the same
print(new_all_in)

          snapnum  phkey         x         y          z          vx  \
1               0      0  0.289189  0.130278   0.456327    7.491590   
3               0      0  0.240575  0.396040   0.038927   67.365524   
4               0      0  0.408888  0.367119   0.182086  -14.317771   
5               0      0  0.403685  0.353911   0.453980  -10.978485   
6               0      0  0.093024  0.249419   0.381685   53.162210   
...           ...    ...       ...       ...        ...         ...   
19682987        0  32767  0.331488  0.464647  62.296314   51.349228   
19682990        0  32767  0.153362  0.597256  62.431736  117.202385   
19682992        0  32767  0.103794  0.421021  62.249700  137.453460   
19682998        0  32767  0.155790  0.036591  62.291122   68.368500   
19682999        0      0  0.052702  0.014002   0.020630   72.956330   

                 vy          vz        id  In_halo  halo_mass  id-prime  
1        -184.12308   35.697285         2     24.0      25323         2  

In [61]:
new_all_in = new_all_in.drop(columns = 'id-prime')
new_all_in

snapnum  phkey         x         y          z          vx  \
1               0      0  0.289189  0.130278   0.456327    7.491590   
3               0      0  0.240575  0.396040   0.038927   67.365524   
4               0      0  0.408888  0.367119   0.182086  -14.317771   
5               0      0  0.403685  0.353911   0.453980  -10.978485   
6               0      0  0.093024  0.249419   0.381685   53.162210   
...           ...    ...       ...       ...        ...         ...   
19682987        0  32767  0.331488  0.464647  62.296314   51.349228   
19682990        0  32767  0.153362  0.597256  62.431736  117.202385   
19682992        0  32767  0.103794  0.421021  62.249700  137.453460   
19682998        0  32767  0.155790  0.036591  62.291122   68.368500   
19682999        0      0  0.052702  0.014002   0.020630   72.956330   

                 vy          vz        id  In_halo  halo_mass  
1        -184.12308   35.697285         2     24.0      25323  
3        -224.21112  142.792710         4     24.0      25323  
4        -216.64820  106.450930         5     40.0      78803  
5        -175.23528   60.103592         6     24.0      25323  
6        -218.81932   74.182014         7     24.0      25323  
...             ...         ...       ...      ...        ...  
19682987 -208.98392  216.752010  19682988     24.0      25323  
19682990 -238.00256  170.423030  19682991     24.0      25323  
19682992 -211.13176  259.363560  19682993     24.0      25323  
19682998 -176.46188  246.383300  19682999     24.0      25323  
19682999 -200.96982  219.741710  19683000     24.0      25323  

[5578120 rows x 11 columns]

In [62]:
all_out['halo_mass'] = 0
all_out.describe()

C:\Users\Saba\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


snapnum         phkey             x             y             z  \
count  14104880.0  1.410488e+07  1.410488e+07  1.410488e+07  1.410488e+07   
mean          0.0  1.657163e+04  3.076424e+01  3.135096e+01  3.197228e+01   
std           0.0  9.590677e+03  1.792420e+01  1.786533e+01  1.837676e+01   
min           0.0  0.000000e+00  5.066395e-07  0.000000e+00  3.213994e-06   
25%           0.0  7.951000e+03  1.526751e+01  1.599329e+01  1.566373e+01   
50%           0.0  1.720200e+04  3.008903e+01  3.164755e+01  3.272449e+01   
75%           0.0  2.494400e+04  4.651848e+01  4.642567e+01  4.813150e+01   
max           0.0  3.276700e+04  6.250000e+01  6.250000e+01  6.250000e+01   

                 vx            vy            vz            id     In_halo  \
count  1.410488e+07  1.410488e+07  1.410488e+07  1.410488e+07  14104880.0   
mean   1.496038e+00  1.384716e-01 -2.378287e+00  9.959007e+06         0.0   
std    2.355148e+02  2.084815e+02  2.840168e+02  5.763869e+06         0.0   
min   -9.406730e+02 -1.006385e+03 -9.354628e+02  1.000000e+00         0.0   
25%   -1.562011e+02 -1.398499e+02 -2.193833e+02  4.768669e+06         0.0   
50%    9.478855e-01  9.944861e-01 -7.136289e+00  1.034783e+07         0.0   
75%    1.612966e+02  1.432975e+02  2.076913e+02  1.498958e+07         0.0   
max    8.930905e+02  9.109451e+02  1.041049e+03  1.968300e+07         0.0   

        halo_mass  
count  14104880.0  
mean          0.0  
std           0.0  
min           0.0  
25%           0.0  
50%           0.0  
75%           0.0  
max           0.0

In [63]:
print(new_all_in)
print(all_out)

          snapnum  phkey         x         y          z          vx  \
1               0      0  0.289189  0.130278   0.456327    7.491590   
3               0      0  0.240575  0.396040   0.038927   67.365524   
4               0      0  0.408888  0.367119   0.182086  -14.317771   
5               0      0  0.403685  0.353911   0.453980  -10.978485   
6               0      0  0.093024  0.249419   0.381685   53.162210   
...           ...    ...       ...       ...        ...         ...   
19682987        0  32767  0.331488  0.464647  62.296314   51.349228   
19682990        0  32767  0.153362  0.597256  62.431736  117.202385   
19682992        0  32767  0.103794  0.421021  62.249700  137.453460   
19682998        0  32767  0.155790  0.036591  62.291122   68.368500   
19682999        0      0  0.052702  0.014002   0.020630   72.956330   

                 vy          vz        id  In_halo  halo_mass  
1        -184.12308   35.697285         2     24.0      25323  
3        -224.21112

In [64]:
frames = [new_all_in , all_out]
all_particles = pd.concat(frames).sort_values('id')
all_particles

snapnum  phkey         x          y          z         vx  \
0               0      0  0.079177   0.003392   0.416711   6.259036   
1               0      0  0.289189   0.130278   0.456327   7.491590   
2               0      0  0.262699   0.197281   0.224564  32.359110   
3               0      0  0.240575   0.396040   0.038927  67.365524   
4               0      0  0.408888   0.367119   0.182086 -14.317771   
...           ...    ...       ...        ...        ...        ...   
19682995        0      0  0.285719   0.102112   0.024742  36.839947   
19682996        0  28086  0.338755  62.488060  62.102010  21.432320   
19682997        0  32767  0.396658   0.143351  62.302100  30.167624   
19682998        0  32767  0.155790   0.036591  62.291122  68.368500   
19682999        0      0  0.052702   0.014002   0.020630  72.956330   

                 vy          vz        id  In_halo  halo_mass  
0        -202.86237   43.663280         1      0.0          0  
1        -184.12308   35.697285         2     24.0      25323  
2        -205.89218   91.230120         3      0.0          0  
3        -224.21112  142.792710         4     24.0      25323  
4        -216.64820  106.450930         5     40.0      78803  
...             ...         ...       ...      ...        ...  
19682995 -176.12938  189.538670  19682996      0.0          0  
19682996 -139.23087  277.197400  19682997      0.0          0  
19682997 -154.33218  236.008880  19682998      0.0          0  
19682998 -176.46188  246.383300  19682999     24.0      25323  
19682999 -200.96982  219.741710  19683000     24.0      25323  

[19683000 rows x 11 columns]

In [65]:
all_particles.to_csv(r'C:\Users\Saba\Documents\ML project\Full_particle_Data\multiclass_labeling_full_information.csv' , sep = ',' , encoding='utf-8', index=False)
print('Data made')

Data made


In [2]:
full_data = pd.read_csv(r'C:\Users\Saba\Documents\ML project\Full_particle_Data\multiclass_labeling_full_information.csv')
full_data.info()
full_data.describe()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19683000 entries, 0 to 19682999
Data columns (total 11 columns):
snapnum      int64
phkey        int64
x            float64
y            float64
z            float64
vx           float64
vy           float64
vz           float64
id           int64
In_halo      float64
halo_mass    int64
dtypes: float64(7), int64(4)
memory usage: 1.6 GB


snapnum         phkey             x             y             z  \
count  19683000.0  1.968300e+07  1.968300e+07  1.968300e+07  1.968300e+07   
mean          0.0  1.637668e+04  3.127470e+01  3.124592e+01  3.122501e+01   
std           0.0  9.453553e+03  1.804878e+01  1.804944e+01  1.802320e+01   
min           0.0  0.000000e+00  5.066395e-07  0.000000e+00  3.213994e-06   
25%           0.0  8.202000e+03  1.564608e+01  1.561590e+01  1.563889e+01   
50%           0.0  1.635500e+04  3.130093e+01  3.123225e+01  3.119702e+01   
75%           0.0  2.455900e+04  4.690146e+01  4.689474e+01  4.681961e+01   
max           0.0  3.276700e+04  6.250000e+01  6.250000e+01  6.250000e+01   

                 vx            vy            vz            id       In_halo  \
count  1.968300e+07  1.968300e+07  1.968300e+07  1.968300e+07  1.968300e+07   
mean  -2.781189e-04  2.267425e-04 -4.716782e-05  9.841500e+06  5.416365e+00   
std    2.414422e+02  2.154665e+02  2.888102e+02  5.681993e+06  1.173987e+01   
min   -9.472481e+02 -1.023661e+03 -9.789142e+02  1.000000e+00  0.000000e+00   
25%   -1.623357e+02 -1.451293e+02 -2.172641e+02  4.920751e+06  0.000000e+00   
50%    6.388357e-01  3.100713e-01 -3.280887e+00  9.841500e+06  0.000000e+00   
75%    1.639600e+02  1.479353e+02  2.112060e+02  1.476225e+07  2.000000e+00   
max    8.930905e+02  9.109451e+02  1.070528e+03  1.968300e+07  4.000000e+01   

          halo_mass  
count  1.968300e+07  
mean   8.145263e+03  
std    2.152317e+04  
min    0.000000e+00  
25%    0.000000e+00  
50%    0.000000e+00  
75%    3.079000e+03  
max    1.372720e+05

In [21]:
#making data equal in size:

id_in_halo = np.array(full_data[['id', 'In_halo', 'halo_mass']])
print(len(id_in_halo))

19683000


In [22]:
len(id_in_halo[id_in_halo[:,1] == 40])

1240545

In [ ]:
random_subset = gapminder.sample(n=3)